# 🏠🏠🏠 Projet Kaggle : Régression : Premières modélisations 🏠🏠🏠

## Initialisation

### Importation des bibliothèques nécessaires


In [1]:
import json

import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
import statsmodels.api as sm
import statsmodels.formula.api as smf
from optbinning import ContinuousOptimalBinning, ContinuousOptimalBinning2D
from sklearn.metrics import (
    max_error,
    mean_absolute_error,
    median_absolute_error,
    r2_score,
    root_mean_squared_error,
)
from sklearn.model_selection import train_test_split

(CVXPY) Feb 21 01:31:10 PM: Encountered unexpected exception importing solver GLOP:
RuntimeError('Unrecognized new version of ortools (9.11.4210). Expected < 9.10.0. Please open a feature request on cvxpy to enable support for this version.')
(CVXPY) Feb 21 01:31:10 PM: Encountered unexpected exception importing solver PDLP:
RuntimeError('Unrecognized new version of ortools (9.11.4210). Expected < 9.10.0. Please open a feature request on cvxpy to enable support for this version.')


In [2]:
with open("../data/processed/dtype_dict.json") as f:
    dtype_dict = json.load(f)

train = pd.read_csv(
    "../data/processed/train.csv",
    delimiter=",",
    encoding="utf-8",
    index_col="Id",
    dtype=dtype_dict,
)

test = pd.read_csv(
    "../data/processed/test.csv",
    delimiter=",",
    encoding="utf-8",
    index_col="Id",
    dtype=dtype_dict,
)

## Choix du modèle

### Gestion des surfaces


In [3]:
train[["1stFlrSF", "2ndFlrSF", "GrLivArea"]].head(15)

1stFlrSF  2ndFlrSF  GrLivArea
Id                               
1        856       854       1710
2       1262         0       1262
3        920       866       1786
4        961       756       1717
5       1145      1053       2198
6        796       566       1362
7       1694         0       1694
8       1107       983       2090
9       1022       752       1774
10      1077         0       1077
11      1040         0       1040
12      1182      1142       2324
13       912         0        912
14      1494         0       1494
15      1253         0       1253

Pour éviter un problème de multi-colinéarité, je pense n'utiliser que GrLivArea. L'information sur l'étage ou non est donnée par MSSubClass par exemple.

### Stacking de modèle ?

Je pensais faire 4 modèles différents :

- La maison présente un sous-sol et un garage.
- La maison ne présente pas de garage.
- La maison ne présente pas de sous-sol.
- La maison ne présente ni garage ni sous-sol.

Pour cela, il faut d'abord s'assurer du volume de données dans chaque sous-catégorie.

#### Les maisons sans sous-sol


In [4]:
train["TotalBsmtSF"][train["TotalBsmtSF"] == 0].count()

37

#### Les maisons sans garage


In [5]:
train["GarageArea"][train["GarageArea"] == 0].count()

81

#### Les maisons sans rien


In [6]:
train["GarageArea"][(train["GarageArea"] == 0) & (train["TotalBsmtSF"] == 0)].count()

7

Il n'y a pas assez de volume ici. Sinon il y a la possibilité de raisonner par quartier.

#### Les volumes par quartier


In [7]:
train["Neighborhood"].value_counts()

Neighborhood
North Ames                               225
College Creek                            150
Old Town                                 113
Edwards                                  100
Somerset                                  86
Gilbert                                   79
Northridge Heights                        77
Sawyer                                    74
Northwest Ames                            73
Sawyer West                               59
Brookside                                 58
Crawford                                  51
Mitchell                                  49
Northridge                                41
Timberland                                38
Iowa DOT and Rail Road                    37
Clear Creek                               28
Stone Brook                               25
South & West of Iowa State University     25
Meadow Village                            17
Bloomington Heights                       17
Briardale                                 

#### Les volumes pour les agrégations de quartier proposé


In [8]:
train["Neighborhood_agg"].value_counts()

Neighborhood_agg
North Ames                    504
Center and university         263
South and west Ames           244
Est Ames                      233
Green and Natural Areas        76
High-End Residential Areas     74
South Est Ames                 66
Name: count, dtype: int64

Je pense qu'il n'y a pas assez de volume encore une fois. L'agrégation proposée pourrait être une piste. On pourrait également raisonner par quartier de luxe, quartier populaire, etc. Je vais donc partir sur un modèle pour tous les cas de figure.

### Quel estimateur ?

Je vais partir sur un GLM, car, d'après les premières analyses, il y a hétéroscédasticité.

### Quelle famille de distribution pour Y, le prix des maisons ?

Pour modéliser SalePrice avec un modèle linéaire généralisé (GLM), il est important de choisir une distribution qui reflète la nature des données. La distribution des prix de vente semble être asymétrique à droite (distribution à queue lourde), ce qui est typique pour les données de prix (voir [ici](/notebooks/04-Projet-Kaggle-Présentation-Storytelling.ipynb), dans la partie "Quelle répartition de prix de vente"). J'ai donc choisi une distribution Gamma.

### Quelle sélection pour le premier modèle ?

Compte tenu des premiers notebooks, voici une synthèse de mes choix :

- Pour l'ensemble des variables de type notes, je vais utiliser d'abord les variables telles quelles. Je testerai ensuite l'encodage ordinal.
- Pour les variables de surfaces, je vais utiliser TotalBsmtSF, GrLivArea, GarageArea, LotFrontage et LotArea (ce qui élimine pas mal de variables quantitatives et d'agrégation).
- Je vais utiliser l'agrégation de certaines variables catégorielles pour avoir des volumes suffisants.
- Pour ce qui est de la configuration de la maison, je vais utiliser une agrégation de HouseStyle. L'information sur la date de la maison, je ne la veux que dans HouseAgeAtSale, et Fin/Unf entrera dans d'autres variables, par exemple les notes de qualité.
- Je vais utiliser Neighborhood d'abord tel quel, ce qui laissera la possibilité de le réagreger (ou d'utiliser l'agrégation existante).
- La variable HouseAgeAtSale va être introduite, avec la variable YrSold (voir les explications [ici](/notebooks/00-Projet-Kaggle-Lecture-et-nettoyage.ipynb) dans la partie remarque)

### La liste complète :

- Quantitatives : TotalBsmtSF, GrLivArea, GarageArea, LotFrontage, LotArea, BedroomAbvGr, HalfBath, FullBath, HouseAgeAtSale,
- Qualitatives : LotShape_agg, LotConfig_agg, HeatingQC_agg, GarageQual_agg, FireplaceQu_agg, KitchenQual, BsmtFullBath_optb, BsmtExposure, BsmtQual, Foundation, ExterQual, Exterior1st_agg, Exterior2nd_agg, OverallQual_agg, Neighborhood, HouseStyle, MSZoning, BsmtFinType1, LandContour, CentralAir, YrSold

### Encodage de HouseStyle


In [9]:
for df in [train, test]:
    df["HouseStyle_agg"] = df["HouseStyle"].replace(
        {"2.5Unf": "2.5", "2.5Fin": "2.5", "1.5Unf": "1.5", "1.5Fin": "1.5"}
    )

### Découpage de variables

#### Création des fonctions de découpage avec Optbinning


In [10]:
# Optimisation du découpage pour une seule variable en fonction d'une target
def bin_feat_1d(
    bin_variable: str,
    bin_target: str,
    df_train: pd.DataFrame,
    df_test: pd.DataFrame,
    transformed_variable_name: str,
    quanti_quali: str,
):
    x = df_train[bin_variable].values

    y = df_train[bin_target].values

    optb_name = "optb_" + bin_variable

    if quanti_quali == "quanti":
        optb_name = ContinuousOptimalBinning(name=bin_variable, dtype="numerical")

    elif quanti_quali == "quali":
        optb_name = ContinuousOptimalBinning(name=bin_variable, dtype="categorical")

    else:
        print('Veuillez renseigner "quanti" ou "quali"')

    optb_name.fit(x, y)

    if optb_name.status != "OPTIMAL":
        print("L'algorithme n'a pas réussi a converger")

    else:
        df_train[transformed_variable_name] = optb_name.transform(x, metric="bins")

        x = df_test[bin_variable].values

        df_test[transformed_variable_name] = optb_name.transform(x, metric="bins")


# Optimisation du découpage pour deux variables (meilleur combinaison de découpage) en fonction d'une target
def bin_feat_2d(
    bin_variable_x: str,
    bin_variable_y: str,
    bin_target: str,
    df_train: pd.DataFrame,
    df_test: pd.DataFrame,
    transformed_variable_name: str,
    quanti_quali_x: str,
    quanti_quali_y: str,
):
    x = df_train[bin_variable_x].values

    y = df_train[bin_variable_y].values

    z = df_train[bin_target].values

    optb_name = "optb_" + bin_variable_x + "_" + bin_variable_y

    if quanti_quali_x == "quanti":
        if quanti_quali_y == "quanti":
            optb_name = ContinuousOptimalBinning2D(
                name_x=bin_variable_x,
                name_y=bin_variable_y,
                dtype_x="numerical",
                dtype_y="numerical",
            )

        elif quanti_quali_y == "quali":
            optb_name = ContinuousOptimalBinning2D(
                name_x=bin_variable_x,
                name_y=bin_variable_y,
                dtype_x="numerical",
                dtype_y="categorical",
            )

    elif quanti_quali_x == "quali":
        if quanti_quali_y == "quanti":
            optb_name = ContinuousOptimalBinning2D(
                name_x=bin_variable_x,
                name_y=bin_variable_y,
                dtype_x="categorical",
                dtype_y="numerical",
            )

        elif quanti_quali_y == "quali":
            optb_name = ContinuousOptimalBinning2D(
                name_x=bin_variable_x,
                name_y=bin_variable_y,
                dtype_x="categorical",
                dtype_y="categorical",
            )

    else:
        print(
            'Veuillez renseigner "quanti" ou "quali" pour selectionner le bon algorithme de découpage, respectivement pour x et y'
        )

    optb_name.fit(x, y, z)

    if optb_name.status != "OPTIMAL":
        print("L'algorithme n'a pas réussi a converger")

    else:
        # Découpage de X
        df_train[transformed_variable_name] = optb_name.transform(x, y, metric="bins")

        x = df_test[bin_variable_x].values

        y = df_test[bin_variable_y].values

        df_test[transformed_variable_name] = optb_name.transform(x, y, metric="bins")

### Séparation en train test


In [11]:
df_train, df_test = train_test_split(
    train,
    test_size=0.33,
    random_state=42,
)

## Première régression

### Création de la formule


In [12]:
selection = [
    "TotalBsmtSF",
    "GrLivArea",
    "GarageArea",
    "LotFrontage",
    "LotArea",
    "BedroomAbvGr",
    "HalfBath",
    "FullBath",
    "LotShape_agg",
    "LotConfig_agg",
    "HeatingQC_agg",
    "GarageQual_agg",
    "FireplaceQu_agg",
    "KitchenQual",
    "BsmtFullBath_optb",
    "BsmtExposure",
    "BsmtQual",
    "Foundation",
    "ExterQual",
    "Exterior1st_agg",
    "Exterior2nd_agg",
    "OverallQual_agg",
    "Neighborhood",
    "HouseStyle_agg",
    "MSZoning",
    "BsmtFinType1",
    "LandContour",
    "CentralAir",
    "HouseAgeAtSale",
    "YrSold",
]

debut_formule = "SalePrice ~"

debut_cat = " + C("

fin_cat = ")"

formule = debut_formule

for col in selection:
    if pd.api.types.is_any_real_numeric_dtype(train[col]):
        formule = str(formule) + " + " + str(col)
    elif train[col].dtype == "object":
        formule = str(formule) + debut_cat + str(col) + fin_cat

### Définition du modèle


In [13]:
reg1 = smf.glm(
    formula=formule,
    data=df_train,
    family=sm.families.Gamma(link=sm.families.links.Identity()),
)

c:\Users\guill\miniconda3\envs\house-prices-env\Lib\site-packages\statsmodels\genmod\generalized_linear_model.py:308: DomainWarning: The Identity link function does not respect the domain of the Gamma family.
  warnings.warn((f"The {type(family.link).__name__} link function "


### Entrainement du modèle


In [14]:
res1 = reg1.fit()

### Analyse globale


In [15]:
print(res1.summary())

                 Generalized Linear Model Regression Results                  
Dep. Variable:              SalePrice   No. Observations:                  978
Model:                            GLM   Df Residuals:                      871
Model Family:                   Gamma   Df Model:                          106
Link Function:               Identity   Scale:                        0.015654
Method:                          IRLS   Log-Likelihood:                -11104.
Date:                Fri, 21 Feb 2025   Deviance:                       14.815
Time:                        13:31:14   Pearson chi2:                     13.6
No. Iterations:                    23   Pseudo R-squ. (CS):             0.9999
Covariance Type:            nonrobust                                         
                                                                       coef    std err          z      P>|z|      [0.025      0.975]
-----------------------------------------------------------------------------

### Remarques :

#### Point de vue global :

Quelques coefficients montrent des incohérences. Par exemple, si BedroomAbvGr augmente d'une unité (1 chambre en plus), alors le prix diminue de 130 $. Je pense que nous avons clairement un modèle non-valide. Il faut enlever des variables et tester de nouvelles choses.

#### Variables catégorielles non-significatives :

- LotShape_agg
- Exterior2nd_agg
- YrSold
- BsmtFullBath_optb

#### Variables catégorielles comprenant au moins une modalité avec un coefficient significatif :

- LotConfig_agg
- HeatingQC_agg
- GarageQual_agg
- FireplaceQu_agg
- KitchenQual
- BsmtFullBath_optb
- BsmtExposure
- BsmtQual
- Foundation
- Exterior1st_agg
- HouseStyle
- MSZoning
- BsmtFinType1
- LandContour
- CentralAir

#### Variables catégorielles à regrouper :

- Neighborhood

#### Variables quantitatives non-significatives :

- BedroomAbvGr
- LotFrontage (au seuil de significativité)
- FullBath (au seuil de significativité)

#### Quelques tests à effectuer :

- HouseStyle et GrLivArea peuvent être enlevés et remplacés par 1stFlrSF et 2ndFlrSF (qui donnent la même surface que GrLivArea en les additionnant et fournissent l'information sur l'étage).
- Regroupement de Neighborhood, avec les quartiers chers, les quartiers moins chers et le reste.
- LotShape_agg, Exterior2nd_agg et BsmtFullBath_optb vont être enlevés.
- Les notations ordinales, quand cela est possible, peuvent être testées à la place des variables catégorielles.
- BedroomAbvGr va subir un découpage. Les deux autres variables quantitatives qui sont au seuil de significativité seront conservées dans un premier temps. J'ai la conviction qu'elles sont importantes.
- LandContour va être enlevé. C'est discutable, mais je pense que l'information va rentrer dans le quartier.

### Critère AIC


In [16]:
res1.aic

22422.37287359281

### Critère BIC


In [17]:
res1.bic_llf

22945.122408286534

### Analyse des résidus

#### Définition des différents thèmes pour les figures plotly


In [18]:
# Template personnalisé
monTheme = go.layout.Template(
    layout=dict(
        template="simple_white",
        autosize=True,
        font=dict(family="Arial", size=15, color="#000000"),
        title=dict(font=dict(size=35, family="Arial"), x=0.5),
        xaxis=dict(tickangle=-35, automargin=True),
        yaxis=dict(tickangle=-35, automargin=True),
    )
)

# Enregistrement du template
pio.templates["monTheme"] = monTheme

# Définition du template comme template par défaut
pio.templates.default = "monTheme"

# Même principe, style de boutons par defaut
# Ne peut pas rentrer dans les templates
styleBoutons = dict(
    bgcolor="#6B6B6B",
    bordercolor="#000000",
    borderwidth=1.5,
    direction="right",
    font_weight=700,
    showactive=True,
    type="buttons",
    x=1,
    xanchor="right",
    y=1.2,
    yanchor="top",
)

mesPolices = {
    "font-size": 25,
    "font-family": "Arial",
    "font-weight": 700,
    "color": "Black",
}

rouge = "rgb(200, 10, 10)"

res = "Résidus"

#### Ajout des résidus dans un dataframe pour plus de simplicité


In [19]:
df_train["residus"] = res1.resid_deviance

#### Forme des résidus

Il s'agit de vérifier que les résidus sont centrés en zéro, symétriques (loi normale centrée réduite)


In [20]:
residuals_density = px.histogram(
    df_train, x="residus", marginal="box", color_discrete_sequence=[rouge]
)

residuals_density.update_layout(
    title_text="Répartition des résidus",
    xaxis_title=res,
    yaxis_title="Nombre",
    showlegend=False,
)

residuals_density.show()

On voit que c'est le cas ici, avec quelques importants, qu'il faudra vérifier par la suite.

#### Résidus en fonction du Prix de vente


In [21]:
scat_res_price = px.scatter(
    df_train,
    x="SalePrice",
    y="residus",
    color_discrete_sequence=[rouge],
)

scat_res_price.update_layout(
    title_text="Résidus en fonction du Prix des maisons",
    xaxis_title="Prix de vente",
    yaxis_title=res,
)

scat_res_price.show()

Il n'y a pas de forme spécifique. Pour les maisons ayant un prix élevé, les résidus semblent plutôt positifs. Ce point reste à vigiler.

#### Résidus en fonction des variables quantitatives sélectionnées

##### Définition de la figure


In [22]:
# Définition de la figure type nuages de points
scat = go.Figure(
    go.Scatter(
        x=df_train["TotalBsmtSF"],
        y=df_train["residus"],
        mode="markers",
        marker_color=rouge,
    )
)

##### Création des boutons pour mise à jour


In [23]:
numerical_cols = [
    col for col in selection if pd.api.types.is_any_real_numeric_dtype(df_train[col])
]

boutons_x = [
    dict(
        label=f"x - {x}",
        method="update",
        args=[
            {"x": [df_train[x]]},
            {"xaxis": {"title": x}},
        ],
    )
    for x in numerical_cols
]

##### Affichage de la figure


In [24]:
# Mise à jour du layout
scat.update_layout(
    title_text="Relation entre les résidus et la variable quantitative séléctionnée",
    xaxis_title="TotalBsmtSF",
    yaxis_title=res,
    updatemenus=[
        dict(
            buttons=boutons_x,
            direction="up",  # Set to 'down' or 'up' for dropdown
            showactive=True,
            x=1,
            xanchor="right",
            y=-0.25,
            yanchor="bottom",  # Custom styles specified here
            bgcolor=styleBoutons["bgcolor"],
            bordercolor=styleBoutons["bordercolor"],
            borderwidth=styleBoutons["borderwidth"],
        ),
    ],
)

# Affichage de la figure
scat.show()

#### Résidus en fonction des variables qualitatives sélectionnées

##### Définition de la figure


In [25]:
violin = go.Figure(
    go.Violin(
        x=df_train["LotShape_agg"],
        y=df_train["residus"],
        fillcolor=rouge,
        line_color="black",
        marker_color="black",
        box_visible=True,
        meanline_visible=True,
    )
)

##### Création des boutons pour mise à jour


In [26]:
categorical_cols = [col for col in selection if df_train[col].dtype == "object"]

boutons_y = [
    dict(
        label=f"x - {x}",
        method="update",
        args=[
            {"x": [df_train[x]]},
            {"xaxis": {"title": x}},
        ],
    )
    for x in categorical_cols
]

##### Affichage de la figure


In [27]:
# Mise à jour du layout
violin.update_layout(
    title_text="Relation entre les résidus et la variable qualitative sélectionnée",
    xaxis_title="LotShape_agg",
    yaxis_title=res,
    updatemenus=[
        dict(
            buttons=boutons_y,
            direction="up",  # Set to 'down' or 'up' for dropdown
            showactive=True,
            x=1,
            xanchor="right",
            y=-0.25,
            yanchor="bottom",  # Custom styles specified here
            bgcolor=styleBoutons["bgcolor"],
            bordercolor=styleBoutons["bordercolor"],
            borderwidth=styleBoutons["borderwidth"],
        ),
    ],
)

# Affichage de la figure
violin.show()

NB : Après analyse des résidus, j'ai envie de laisser mes variables quantitatives et de ne pas les découper. Je pense qu'il y a en réalité un décrochage pour les maisons extrêmement grandes par exemple, mais dans la zone d'observation des surfaces, ça ne semble pas poser de problèmes.

## Deuxième régression

### Découpage de Neighborhood


In [28]:
neighborhoods_to_keep = [
    "Brookside",
    "Clear Creek",
    "Crawford",
    "Northridge",
    "Northridge Heights",
    "Stone Brook",
    "Veenker",
]

for df in [df_train, df_test]:
    df["Neighborhood_agg2"] = np.where(
        df["Neighborhood"].isin(neighborhoods_to_keep), df["Neighborhood"], "Autre"
    )

### Découpage de BedroomAbvGr


In [29]:
bin_feat_1d(
    "BedroomAbvGr", "SalePrice", df_train, df_test, "BedroomAbvGr_optb", "quanti"
)

In [30]:
df_train["BedroomAbvGr_optb"].value_counts()

BedroomAbvGr_optb
[2.50, 3.50)    533
(-inf, 2.50)    273
[3.50, inf)     172
Name: count, dtype: int64

In [31]:
for col in train.columns:
    if col.endswith("_ord"):
        print(col)

LotShape_ord
LandContour_ord
Utilities_ord
LandSlope_ord
OverallQual_ord
OverallCond_ord
ExterQual_ord
ExterCond_ord
BsmtQual_ord
BsmtCond_ord
HeatingQC_ord
KitchenQual_ord
FireplaceQu_ord
GarageQual_ord
GarageCond_ord
PoolQC_ord
BsmtExposure_ord
BsmtFinType1_ord
BsmtFinType2_ord
Functional_ord
GarageFinish_ord


### Nouvelle selection


In [32]:
df_train["HeatingQC_ord"].value_counts()

HeatingQC_ord
5    498
3    281
4    161
2     37
1      1
Name: count, dtype: int64

In [33]:
# Renommage obligatoire des colonnes
for df in [df_train, df_test]:
    df.rename(
        columns={"1stFlrSF": "FirstFlrSF", "2ndFlrSF": "SecondFlrSF"}, inplace=True
    )

selection = [
    "TotalBsmtSF",
    "FirstFlrSF",
    "SecondFlrSF",
    "GarageArea",
    "LotFrontage",
    "LotArea",
    "BedroomAbvGr_optb",
    "HalfBath",
    "FullBath",
    "LotConfig_agg",
    "HeatingQC_ord",
    "GarageQual_ord",
    "FireplaceQu_ord",
    "KitchenQual_ord",
    "BsmtExposure_ord",
    "BsmtQual_ord",
    "Foundation",
    "ExterQual_ord",
    "Exterior1st_agg",
    "OverallQual_ord",
    "Neighborhood_agg2",
    "MSZoning",
    "BsmtFinType1_ord",
    "CentralAir",
    "HouseAgeAtSale",
]

formule = debut_formule

for col in selection:
    if pd.api.types.is_any_real_numeric_dtype(df_train[col]) or col.endswith("_ord"):
        formule = str(formule) + " + " + str(col)
    else:
        formule = str(formule) + debut_cat + str(col) + fin_cat

### Définition du modèle


In [34]:
reg2 = smf.glm(
    formula=formule,
    data=df_train,
    family=sm.families.Gamma(link=sm.families.links.Identity()),
)

c:\Users\guill\miniconda3\envs\house-prices-env\Lib\site-packages\statsmodels\genmod\generalized_linear_model.py:308: DomainWarning:

The Identity link function does not respect the domain of the Gamma family.



### Entrainement du modèle


In [35]:
res2 = reg2.fit()

### Analyse Globale


In [36]:
print(res2.summary())

                 Generalized Linear Model Regression Results                  
Dep. Variable:              SalePrice   No. Observations:                  978
Model:                            GLM   Df Residuals:                      914
Model Family:                   Gamma   Df Model:                           63
Link Function:               Identity   Scale:                        0.016521
Method:                          IRLS   Log-Likelihood:                -11153.
Date:                Fri, 21 Feb 2025   Deviance:                       16.381
Time:                        13:31:19   Pearson chi2:                     15.1
No. Iterations:                    17   Pseudo R-squ. (CS):             0.9998
Covariance Type:            nonrobust                                         
                                                              coef    std err          z      P>|z|      [0.025      0.975]
--------------------------------------------------------------------------------------

### Encore beaucoup de variables/modalités non-significatives

Je vais repartir sur un modèle beaucoup plus simple. J'enlève :

- BedroomAbvGr_optb
- HeatingQC_ord
- FireplaceQu_ord
- Foundation

Je remets certaines notes agrégées :

- ExterQual_ord -> ExterQual
- GarageQual_ord -> GarageQual_agg
- KitchenQual_ord -> KitchenQual
- BsmtQual_ord -> BsmtQual

Je teste une variable différente pour la cheminé :

- Fireplaces_optb

## Troisième régression

### Nouvelle sélection


In [37]:
selection = [
    "TotalBsmtSF",
    "FirstFlrSF",
    "SecondFlrSF",
    "GarageArea",
    "LotFrontage",
    "LotArea",
    "HalfBath",
    "FullBath",
    "LotConfig_agg",
    "GarageQual_agg",
    "Fireplaces_optb",
    "KitchenQual",
    "BsmtExposure_ord",
    "BsmtQual",
    "ExterQual",
    "Exterior1st_agg",
    "OverallQual_ord",
    "Neighborhood_agg2",
    "MSZoning",
    "BsmtFinType1_ord",
    "CentralAir",
    "HouseAgeAtSale",
]

formule = debut_formule

for col in selection:
    if pd.api.types.is_any_real_numeric_dtype(df_train[col]) or col.endswith("_ord"):
        formule = str(formule) + " + " + str(col)
    else:
        formule = str(formule) + debut_cat + str(col) + fin_cat

### Définition du modèle


In [38]:
reg3 = smf.glm(
    formula=formule,
    data=df_train,
    family=sm.families.Gamma(link=sm.families.links.Identity()),
)

c:\Users\guill\miniconda3\envs\house-prices-env\Lib\site-packages\statsmodels\genmod\generalized_linear_model.py:308: DomainWarning:

The Identity link function does not respect the domain of the Gamma family.



### Entrainement du modèle


In [39]:
res3 = reg3.fit()

### Analyse Globale


In [40]:
print(res3.summary())

                 Generalized Linear Model Regression Results                  
Dep. Variable:              SalePrice   No. Observations:                  978
Model:                            GLM   Df Residuals:                      930
Model Family:                   Gamma   Df Model:                           47
Link Function:               Identity   Scale:                        0.016651
Method:                          IRLS   Log-Likelihood:                -11167.
Date:                Fri, 21 Feb 2025   Deviance:                       16.838
Time:                        13:31:19   Pearson chi2:                     15.5
No. Iterations:                    19   Pseudo R-squ. (CS):             0.9998
Covariance Type:            nonrobust                                         
                                                              coef    std err          z      P>|z|      [0.025      0.975]
--------------------------------------------------------------------------------------

Tous les bêtas sont significatifs ou presque. Concernant Fullbath, je vais essayer de rajouter le nombre de salles de bain dans le sous-sol de manière à exposer le nombre de salles de bains total.

## Dernière régression

### Création de FullBath_tot


In [41]:
df_train["BsmtFullBath"].value_counts()

BsmtFullBath
0    576
1    391
2     10
3      1
Name: count, dtype: int64

In [42]:
df_train["FullBath"].value_counts()

FullBath
2    527
1    425
3     23
0      3
Name: count, dtype: int64

In [43]:
for df in [df_train, df_test]:
    df["FullBath_tot"] = df["FullBath"] + df["BsmtFullBath"]
    # en plus je vais essayer de reprendre le même principe avec les toilettes
    df["HalfBath_tot"] = df["HalfBath"] + df["BsmtHalfBath"]

In [44]:
df_test[["FullBath", "BsmtFullBath", "FullBath_tot"]].head(3)

FullBath  BsmtFullBath  FullBath_tot
Id                                        
893          1             0             1
1106         2             1             3
414          1             0             1

In [45]:
df_train["HalfBath_tot"].value_counts()

HalfBath_tot
0    573
1    384
2     21
Name: count, dtype: int64

NB : HalfBath_tot reste pour moi trop déséquilibré et n'apportera donc pas grand-chose.

### Nouvelle sélection


In [58]:
selection = [
    "TotalBsmtSF",
    "FirstFlrSF",
    "SecondFlrSF",
    "GarageArea",
    "LotFrontage",
    "LotArea",
    "HalfBath_tot",
    "FullBath_tot",
    "LotConfig_agg",
    "GarageQual_agg",
    "Fireplaces_optb",
    "KitchenQual",
    "BsmtExposure_ord",
    "BsmtQual",
    "ExterQual",
    "Exterior1st_agg",
    "OverallQual_ord",
    "Neighborhood_agg2",
    "MSZoning",
    "BsmtFinType1_ord",
    "CentralAir",
    "HouseAgeAtSale",
]

formule = debut_formule

for col in selection:
    if pd.api.types.is_any_real_numeric_dtype(df_train[col]) or col.endswith("_ord"):
        formule = str(formule) + " + " + str(col)
    else:
        formule = str(formule) + debut_cat + str(col) + fin_cat

### Définition du modèle


In [59]:
reg4 = smf.glm(
    formula=formule,
    data=df_train,
    family=sm.families.Gamma(link=sm.families.links.Identity()),
)

c:\Users\guill\miniconda3\envs\house-prices-env\Lib\site-packages\statsmodels\genmod\generalized_linear_model.py:308: DomainWarning:

The Identity link function does not respect the domain of the Gamma family.



### Entrainement du modèle


In [60]:
res4 = reg4.fit()

### Analyse globale


In [61]:
print(res4.summary())

                 Generalized Linear Model Regression Results                  
Dep. Variable:              SalePrice   No. Observations:                  978
Model:                            GLM   Df Residuals:                      930
Model Family:                   Gamma   Df Model:                           47
Link Function:               Identity   Scale:                        0.016648
Method:                          IRLS   Log-Likelihood:                -11167.
Date:                Fri, 21 Feb 2025   Deviance:                       16.859
Time:                        13:33:50   Pearson chi2:                     15.5
No. Iterations:                    19   Pseudo R-squ. (CS):             0.9998
Covariance Type:            nonrobust                                         
                                                              coef    std err          z      P>|z|      [0.025      0.975]
--------------------------------------------------------------------------------------

## Analyses des performances

### Calculs des prédictions


In [62]:
df_test["SalePrice_pred"] = res4.predict(df_test[selection])

In [63]:
df_test[["SalePrice_pred", "SalePrice"]].head(10)

SalePrice_pred  SalePrice
Id                             
893    135403.440513     154500
1106   351495.958937     325000
414    105835.776319     115000
523    164506.934684     159000
1037   317701.213508     315500
615     73544.221221      75500
219    226728.261411     311500
1161   156246.102779     146000
650     77819.106451      84500
888    132972.988427     135500

### Quelques métriques bien connues


In [64]:
res_1_sel = pd.DataFrame(
    {
        "MAE": [mean_absolute_error(df_test["SalePrice"], df_test["SalePrice_pred"])],
        "RMSE": [
            root_mean_squared_error(df_test["SalePrice"], df_test["SalePrice_pred"])
        ],
        "MEE": [median_absolute_error(df_test["SalePrice"], df_test["SalePrice_pred"])],
        "ME": [max_error(df_test["SalePrice"], df_test["SalePrice_pred"])],
        "R2": [r2_score(df_test["SalePrice"], df_test["SalePrice_pred"])],
    }
)


res_1_sel

MAE          RMSE           MEE             ME        R2
0  18049.187524  31003.774583  11666.762586  254903.977337  0.869067

### Quelques commentaires

1. Mean Absolute Error (MAE) : 18 035

- Interprétation : En moyenne, les prédictions de 18 035 $ des vrais prix de vente. Cela signifie que, en moyenne, les prédictions sont décalées de cette valeur par rapport aux valeurs réelles.
- Commentaire : Un MAE de cette ampleur peut être considéré comme acceptable ou non, selon l'échelle de ma cible (SalePrice). Les prix de vente étant généralement de l'ordre de centaines de milliers, cela pourrait être considéré comme une erreur modérée.

2. Root Mean Squared Error (RMSE) : 31 065

- Interprétation : Le RMSE est plus élevé que le MAE, donc le modèle fait des erreurs plus importantes sur certaines prédictions. Cela peut être dû à des valeurs aberrantes ou à des prédictions particulièrement mauvaises pour certaines données.
- Commentaire : La mise au carré de l'erreur rend cet indicateur plus sensible aux grandes erreurs. Cela suggère que certaines prédictions sont significativement éloignées des valeurs réelles.

3. Median Absolute Error (MEE) : 11 529

- Interprétation : La médiane des erreurs absolues est de 11 529, ce qui signifie que la moitié des prédictions ont une erreur inférieure à cette valeur.
- Commentaire : Le MEE étant inférieur au MAE, cela indique que la majorité des erreurs sont plus petites, mais qu'il y a quelques erreurs plus importantes qui augmentent le MAE. Cela rejoint le point précédent. Il s'agit maintenant de comprendre pourquoi et sur quels types de données il y a des erreurs importantes.

4. Max Error (ME) : 256 486

- Interprétation : La plus grande erreur observée est de 256 486 $. Cela représente le pire scénario en termes de précision du modèle.
- Commentaire : Une telle erreur maximale peut être problématique, surtout si elle est fréquente. Il pourrait être utile d'examiner les cas où cette erreur se produit pour comprendre pourquoi le modèle échoue si dramatiquement. Cela rejoint les points précédents.

5. R² Score : 0.8685

- Interprétation : Le coefficient de détermination (R²) indique que 86.85% de la variance des valeurs réelles est expliquée par le modèle.
- Commentaire : Un R² de 0.8685 est généralement considéré comme très bon, indiquant que le modèle capture bien la variance des données. Cependant, il est important de noter que le R² peut être trompeur si le modèle est sur-ajusté. C'est le cas ici. Pour y remédier, il y aura une validation croisée par la suite.

### Quelques Graphiques


In [65]:
df_test["residus"] = df_test["SalePrice"] - df_test["SalePrice_pred"]

#### Forme des résidus


In [92]:
residuals_density = px.histogram(
    df_test, x="residus", marginal="box", color_discrete_sequence=[rouge]
)

residuals_density.update_layout(
    title_text="Répartition des résidus",
    xaxis_title=res,
    yaxis_title="Nombre",
    showlegend=False,
)

residuals_density.show()

#### Résidus en fonction du Prix de vente


In [70]:
scat_res_price = px.scatter(
    df_test,
    x="SalePrice",
    y="residus",
    color_discrete_sequence=[rouge],
)

scat_res_price.update_layout(
    title_text="Résidus (valeur réelle - valeur prédite) en fonction du Prix des maisons",
    xaxis_title="Prix de vente",
    yaxis_title=res,
)

scat_res_price.show()

#### Résidus en fonction des variables quantitatives


In [93]:
# Définition de la figure type nuages de points
scat = go.Figure(
    go.Scatter(
        x=df_test["LotFrontage"],
        y=df_test["residus"],
        mode="markers",
        marker_color=rouge,
    )
)

numerical_cols = [
    col
    for col in df_test.columns
    if pd.api.types.is_any_real_numeric_dtype(df_test[col])
]

boutons_x = [
    dict(
        label=f"x - {x}",
        method="update",
        args=[
            {"x": [df_test[x]]},
            {"xaxis": {"title": x}},
        ],
    )
    for x in numerical_cols
]

# Mise à jour du layout
scat.update_layout(
    title_text="Relation entre les résidus et la variable quantitative séléctionnée",
    xaxis_title="LotFrontage",
    yaxis_title=res,
    updatemenus=[
        dict(
            buttons=boutons_x,
            direction="up",  # Set to 'down' or 'up' for dropdown
            showactive=True,
            x=1,
            xanchor="right",
            y=-0.25,
            yanchor="bottom",  # Custom styles specified here
            bgcolor=styleBoutons["bgcolor"],
            bordercolor=styleBoutons["bordercolor"],
            borderwidth=styleBoutons["borderwidth"],
        ),
    ],
)

# Affichage de la figure
scat.show()

#### Résidus en fonction des variables qualitatives sélectionnées


In [97]:
violin = go.Figure(
    go.Violin(
        x=df_test["MSSubClass"],
        y=df_test["residus"],
        fillcolor=rouge,
        line_color="black",
        marker_color="black",
        box_visible=True,
        meanline_visible=True,
    )
)

categorical_cols = [col for col in df_test.columns if df_test[col].dtype == "object"]

boutons_y = [
    dict(
        label=f"x - {x}",
        method="update",
        args=[
            {"x": [df_test[x]]},
            {"xaxis": {"title": x}},
        ],
    )
    for x in categorical_cols
]

# Mise à jour du layout
violin.update_layout(
    title_text="Relation entre les résidus et la variable qualitative sélectionnée",
    xaxis_title="MSSubClass",
    yaxis_title=res,
    updatemenus=[
        dict(
            buttons=boutons_y,
            direction="up",  # Set to 'down' or 'up' for dropdown
            showactive=True,
            x=1,
            xanchor="right",
            y=-0.25,
            yanchor="bottom",  # Custom styles specified here
            bgcolor=styleBoutons["bgcolor"],
            bordercolor=styleBoutons["bordercolor"],
            borderwidth=styleBoutons["borderwidth"],
        ),
    ],
)

# Affichage de la figure
violin.show()

Le modèle n'est pas performant pour les maisons au prix élevé. En examinant les surfaces, les résidus sont élevés pour les maisons ayant un étage de grande taille. Ce phénomène est également visible pour l'ensemble des surfaces habitables (GrLivArea), mais moins prononcé pour le rez-de-chaussée uniquement. Deux solutions pourraient être envisagées :

- Encodage de la surface de l'étage en intervalles.
- Stacking avec des modèles distincts :
  1. Un modèle pour les maisons dont la surface de l'étage est inférieure à un certain seuil (à déterminer en fonction du volume et de la forme des résidus).
  2. Un modèle pour les maisons dont la surface de l'étage est supérieure ou égale à ce seuil.

NB : D'un point de vue qualitatif, la présence d'une piscine semble être un facteur pertinent pour ajuster certains prix. Cependant, cette variable est trop déséquilibrée dans le jeu de données. Par conséquent, j'appliquerai un coefficient correctif de manière déterministe.


In [107]:
df_train[selection][(df_train["SecondFlrSF"] >= 700)].describe()

TotalBsmtSF   FirstFlrSF  SecondFlrSF   GarageArea  LotFrontage  \
count   272.000000   272.000000   272.000000   272.000000   272.000000   
mean    984.025735  1080.257353   954.099265   539.106618    59.863971   
std     442.748181   374.382158   222.376898   201.702330    39.260506   
min       0.000000   372.000000   700.000000     0.000000     0.000000   
25%     783.000000   859.500000   787.250000   432.000000    39.750000   
50%     913.500000  1009.500000   882.000000   513.500000    68.000000   
75%    1110.250000  1211.000000  1090.000000   650.000000    80.250000   
max    6110.000000  4692.000000  1818.000000  1418.000000   313.000000   

             LotArea  HalfBath_tot  FullBath_tot  BsmtExposure_ord  \
count     272.000000    272.000000    272.000000        272.000000   
mean    12130.977941      0.863971      2.272059          1.488971   
std     11341.074061      0.462493      0.697565          0.952695   
min      2117.000000      0.000000      1.000000          0.000000   
25%      8753.750000      1.000000      2.000000          1.000000   
50%     10444.000000      1.000000      2.000000          1.000000   
75%     12393.250000      1.000000      3.000000          2.000000   
max    159000.000000      2.000000      4.000000          4.000000   

       OverallQual_ord  BsmtFinType1_ord  HouseAgeAtSale  
count       272.000000        272.000000      272.000000  
mean          5.772059          3.404412       32.161765  
std           1.069310          2.228228       35.053090  
min           2.000000          0.000000        0.000000  
25%           5.000000          1.000000        6.000000  
50%           6.000000          3.000000       14.000000  
75%           6.000000          6.000000       50.000000  
max           9.000000          6.000000      136.000000

In [108]:
df_train["PoolQC"].value_counts()

PoolQC
No pool      974
Good           2
Excellent      1
Fair           1
Name: count, dtype: int64